In [1]:
#初始化
! [ -e /content ] && pip install -Uqq fastbook
import fastbook
fastbook.setup_book()

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 719.8/719.8 kB 12.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 22.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 15.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 17.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 19.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 32.4 MB/s eta 0:00:00
Mounted at /content/gdrive


In [2]:
from fastbook import *
from IPython.display import display,HTML

In [3]:
# 加载IMDB数据集
from fastai.text.all import *
path = untar_data(URLs.IMDB)

In [4]:
files = get_text_files(path, folders = ['train', 'test', 'unsup'])

In [5]:
txt = files[0].open().read(); txt[:75]

'This Movie is complete crap! Avoid this waste of celluloid at all costs, it'

In [6]:
# spacy
spacy = WordTokenizer()
toks = first(spacy([txt]))
print(coll_repr(toks, 30))

(#141) ['This','Movie','is','complete','crap','!','Avoid','this','waste','of','celluloid','at','all','costs',',','it','is','rambling','and','incoherent','.','I','pride','myself','on','plumbing','the','depths','of','70'...]


In [7]:
first(spacy(['The U.S. dollar $1 is $1.00.']))

(#9) ['The','U.S.','dollar','$','1','is','$','1.00','.']

In [8]:
# xxbos :: 表示文本的开始（这里，一篇评论）
# xxmaj :: 表示下一个单词以大写字母开头（因为我们已经将所有内容都转换为小写）
# xxunk :: 表示该词未知
tkn = Tokenizer(spacy)
print(coll_repr(tkn(txt), 31))

(#151) ['xxbos','xxmaj','this','xxmaj','movie','is','complete','crap','!','xxmaj','avoid','this','waste','of','celluloid','at','all','costs',',','it','is','rambling','and','incoherent','.','i','pride','myself','on','plumbing','the'...]


In [9]:
defaults.text_proc_rules

[<function fastai.text.core.fix_html(x)>,
 <function fastai.text.core.replace_rep(t)>,
 <function fastai.text.core.replace_wrep(t)>,
 <function fastai.text.core.spec_add_spaces(t)>,
 <function fastai.text.core.rm_useless_spaces(t)>,
 <function fastai.text.core.replace_all_caps(t)>,
 <function fastai.text.core.replace_maj(t)>,
 <function fastai.text.core.lowercase(t, add_bos=True, add_eos=False)>]

In [10]:
# 子词分词
txts = L(o.open().read() for o in files[:2000])

In [11]:
def subword(sz):
    sp = SubwordTokenizer(vocab_sz=sz)
    sp.setup(txts)
    return ' '.join(first(sp([txt]))[:40])

In [12]:
subword(1000)

'▁This ▁M o v ie ▁is ▁complete ▁crap ! ▁A void ▁this ▁waste ▁of ▁c ell ul o id ▁at ▁all ▁co s t s , ▁it ▁is ▁ ra mb l ing ▁and ▁in co h er ent .'

In [13]:
subword(200)

'▁ T h i s ▁ M o v i e ▁is ▁co m p le t e ▁c ra p ! ▁A v o i d ▁this ▁was t e ▁of ▁c e l l u l o i'

In [14]:
subword(10000)

"▁This ▁Movie ▁is ▁complete ▁crap ! ▁Avoid ▁this ▁waste ▁of ▁celluloid ▁at ▁all ▁costs , ▁it ▁is ▁rambling ▁and ▁incoherent . ▁I ▁pride ▁myself ▁on ▁plumb ing ▁the ▁depth s ▁of ▁70 ' s ▁sleaze ▁cinema ▁from ▁everything ▁from ▁Sa"

In [15]:
# 使用fastai进行数值化
toks = tkn(txt)
print(coll_repr(tkn(txt), 31))

(#151) ['xxbos','xxmaj','this','xxmaj','movie','is','complete','crap','!','xxmaj','avoid','this','waste','of','celluloid','at','all','costs',',','it','is','rambling','and','incoherent','.','i','pride','myself','on','plumbing','the'...]


In [16]:
toks200 = txts[:200].map(tkn)
toks200[0]

(#151) ['xxbos','xxmaj','this','xxmaj','movie','is','complete','crap','!','xxmaj'...]

In [17]:
num = Numericalize()
num.setup(toks200)
coll_repr(num.vocab,20)

"(#1960) ['xxunk','xxpad','xxbos','xxeos','xxfld','xxrep','xxwrep','xxup','xxmaj','the',',','.','a','and','to','of','i','it','is','in'...]"

In [18]:
nums = num(toks)[:20]; nums

TensorText([  2,   8,  20,   8,  27,  18, 313, 240,  44,   8, 616,  20, 196,  15,   0,  48,  47, 843,  10,  17])

In [19]:
' '.join(num.vocab[o] for o in nums)

'xxbos xxmaj this xxmaj movie is complete crap ! xxmaj avoid this waste of xxunk at all costs , it'

In [20]:
# 将我们的文本分批用于语言模型
stream = "In this chapter, we will go back over the example of classifying movie reviews we studied in chapter 1 and dig deeper under the surface. First we will look at the processing steps necessary to convert text into numbers and how to customize it. By doing this, we'll have another example of the PreProcessor used in the data block API.\nThen we will study how we build a language model and train it for a while."
tokens = tkn(stream)
bs,seq_len = 6,15
d_tokens = np.array([tokens[i*seq_len:(i+1)*seq_len] for i in range(bs)])
df = pd.DataFrame(d_tokens)
display(HTML(df.to_html(index=False,header=None)))

In [21]:
bs,seq_len = 6,5
d_tokens = np.array([tokens[i*15:i*15+seq_len] for i in range(bs)])
df = pd.DataFrame(d_tokens)
display(HTML(df.to_html(index=False,header=None)))

In [22]:
bs,seq_len = 6,5
d_tokens = np.array([tokens[i*15+seq_len:i*15+2*seq_len] for i in range(bs)])
df = pd.DataFrame(d_tokens)
display(HTML(df.to_html(index=False,header=None)))

In [23]:
bs,seq_len = 6,5
d_tokens = np.array([tokens[i*15+10:i*15+15] for i in range(bs)])
df = pd.DataFrame(d_tokens)
display(HTML(df.to_html(index=False,header=None)))

In [24]:
nums200 = toks200.map(num)

In [25]:
dl = LMDataLoader(nums200)

In [26]:
x,y = first(dl)
x.shape,y.shape

(torch.Size([64, 72]), torch.Size([64, 72]))

In [27]:
' '.join(num.vocab[o] for o in x[0][:20])

'xxbos xxmaj this xxmaj movie is complete crap ! xxmaj avoid this waste of xxunk at all costs , it'

In [28]:
' '.join(num.vocab[o] for o in y[0][:20])

'xxmaj this xxmaj movie is complete crap ! xxmaj avoid this waste of xxunk at all costs , it is'

In [29]:
# 文本生成器
# 使用 TextBlock 来创建语言模型
get_imdb = partial(get_text_files, folders=['train', 'test', 'unsup'])

dls_lm = DataBlock(
    blocks=TextBlock.from_folder(path, is_lm=True),
    get_items=get_imdb, splitter=RandomSplitter(0.1)
).dataloaders(path, path=path, bs=128, seq_len=80)

/usr/local/lib/python3.10/dist-packages/spacy/util.py:1740: UserWarning: [W111] Jupyter notebook detected: if using `prefer_gpu()` or `require_gpu()`, include it in the same cell right before `spacy.load()` to ensure that the model is loaded on the correct device. More information: http://spacy.io/usage/v3#jupyter-notebook-gpu
  warnings.warn(Warnings.W111)


In [30]:
dls_lm.show_batch(max_n=2)

In [31]:
learn = language_model_learner(
    dls_lm, AWD_LSTM, drop_mult=0.3,
    metrics=[accuracy, Perplexity()]).to_fp16()

In [32]:
learn.fit_one_cycle(1, 2e-2)

In [33]:
learn.save('1epoch')

Path('/root/.fastai/data/imdb/models/1epoch.pth')

In [34]:
learn = learn.load('1epoch')

In [35]:
learn.unfreeze()
learn.fit_one_cycle(10, 2e-3)

In [36]:
learn.save_encoder('finetuned')

In [37]:
# 文本生成
TEXT = "I liked this movie because"
N_WORDS = 40
N_SENTENCES = 2
preds = [learn.predict(TEXT, N_WORDS, temperature=0.75)
         for _ in range(N_SENTENCES)]

In [38]:
print("\n".join(preds))

i liked this movie because it was a " chick flick " which i liked more than others , so i gave it a chance , and even though i am a big fan of Olivia de Havilland , i think that the
i liked this movie because it actually made me smile and once i learned something about the story it really got a lot of fun . i think this movie is real a lot more than the sound track . i have to say that


In [39]:
# 文本分类器
dls_clas = DataBlock(
    blocks=(TextBlock.from_folder(path, vocab=dls_lm.vocab),CategoryBlock),
    get_y = parent_label,
    get_items=partial(get_text_files, folders=['train', 'test']),
    splitter=GrandparentSplitter(valid_name='test')
).dataloaders(path, path=path, bs=128, seq_len=72)

/usr/local/lib/python3.10/dist-packages/spacy/util.py:1740: UserWarning: [W111] Jupyter notebook detected: if using `prefer_gpu()` or `require_gpu()`, include it in the same cell right before `spacy.load()` to ensure that the model is loaded on the correct device. More information: http://spacy.io/usage/v3#jupyter-notebook-gpu
  warnings.warn(Warnings.W111)


In [40]:
dls_clas.show_batch(max_n=3)

In [41]:
nums_samp = toks200[:10].map(num)

In [42]:
nums_samp.map(len)

(#10) [151,449,162,159,302,211,234,169,348,219]

In [43]:
# 创建模型对文本进行分类
learn = text_classifier_learner(dls_clas, AWD_LSTM, drop_mult=0.5,
                                metrics=accuracy).to_fp16()

In [44]:
learn = learn.load_encoder('finetuned')

In [45]:
learn.fit_one_cycle(1, 2e-2)

In [46]:
learn.freeze_to(-2)
learn.fit_one_cycle(1, slice(1e-2/(2.6**4),1e-2))

In [ ]:
learn.freeze_to(-3)
learn.fit_one_cycle(1, slice(5e-3/(2.6**4),5e-3))

In [48]:
learn.unfreeze()
learn.fit_one_cycle(2, slice(1e-3/(2.6**4),1e-3))